# Lecture 13: Advanced NumPy Operations
## Linear Algebra, Random Numbers, and Applications

**INF 605 - Introduction to Programming - Python**  
**Prof. Rongyu Lin**  
**Quinnipiac University**

---

## Learning Objectives

1. Master Matrix Operations (transpose, @, swapaxes)
2. Understand Broadcasting rules
3. Generate Random Numbers with default_rng()
4. Apply Array-Oriented Programming (where, meshgrid)
5. Perform Linear Algebra (polyfit, corrcoef for Assignment 4!)
6. Save/Load Arrays
7. Implement Random Walks simulation

## Prerequisites
From Lectures 12: arrays, indexing, ufuncs, statistics, axis parameter, sorting

## Setup

In [ ]:
import numpy as np
print(f'NumPy {np.__version__}')

---
# Part 1: Transposing and Matrix Operations

Transpose flips rows and columns - imagine rotating a spreadsheet 90 degrees. The .T attribute creates this transformation instantly. Matrix operations like dot products combine arrays through multiplication and summation, fundamental for linear algebra. These operations are building blocks for data science, machine learning, and scientific computing.

## 1.1 Transpose with .T Attribute

The transpose operation swaps rows and columns. A 3x4 array (3 rows, 4 columns) becomes 4x3 (4 rows, 3 columns) after transposing. Think of it like reading a table sideways - what were columns become rows, and vice versa. This is crucial for matrix mathematics and aligning data for operations.

In [ ]:
# Create 2D array
arr = np.array([[1, 2, 3],
                [4, 5, 6]])
print('Original (2x3):')
print(arr)
print('\nTransposed (3x2):')
print(arr.T)

**Result:** Original shape (2, 3) became (3, 2). Row [1,2,3] became column [1,4], row [4,5,6] became [2,5], and [3,6]. Transpose is its own inverse: arr.T.T gives back arr!

### Exercise: Temperature Data Transpose

You have daily temps for 3 cities over 4 days (rows=days, cols=cities). Transpose to get days as columns.

In [ ]:
# Daily temperatures: rows=days, cols=cities
temps = np.array([[72, 68, 75],
                  [75, 70, 78],
                  [71, 67, 73],
                  [78, 72, 80]])
# Your code here:


In [ ]:
# Solution
transposed = temps.T
print(f'Original shape: {temps.shape}')
print(f'Transposed shape: {transposed.shape}')
print('Now rows=cities, cols=days')

**Solution:** Shape changed from (4,3) to (3,4). Each city now has its own row showing temps across all days.

## 1.2 Matrix Multiplication with @ Operator

Matrix multiplication combines arrays through row-by-column multiplication and summation. The @ operator implements true matrix multiplication (different from element-wise *). For shapes (m,n) @ (n,p), result is (m,p). Inner dimensions must match! This is fundamental for linear algebra, neural networks, and scientific computing.

In [ ]:
# Matrix multiplication
A = np.array([[1, 2],
              [3, 4]])
B = np.array([[5, 6],
              [7, 8]])
result = A @ B
print('A:\n', A)
print('B:\n', B)
print('A @ B:\n', result)

**Result:** Element [0,0] = 1*5+2*7=19, [0,1]=1*6+2*8=22, [1,0]=3*5+4*7=43, [1,1]=3*6+4*8=50. Each output element is a dot product of A's row with B's column.

### Exercise: Sales Revenue

You have units sold (2 stores, 3 products) and prices (3 products). Calculate total revenue per store using @.

In [ ]:
units = np.array([[10, 5, 8],   # Store 1
                  [12, 7, 6]])  # Store 2
prices = np.array([20, 30, 15])  # 3 products
# Your code here (hint: prices needs reshape):


In [ ]:
# Solution
revenue = units @ prices.reshape(-1, 1)
print(f'Store revenues: {revenue.flatten()}')

**Solution:** Store 1: 10*20+5*30+8*15=470, Store 2: 12*20+7*30+6*15=540. Matrix multiplication computed total revenue efficiently!

---
# Part 2: Broadcasting Principles

Broadcasting lets NumPy perform operations on arrays of different shapes by automatically expanding smaller arrays. Think of it like filling a multiplication table - you write numbers once on the edges, and the table fills by repeating those values. This eliminates explicit loops and makes code elegant and fast. Broadcasting rules: dimensions must match or one must be 1.

## 2.1 Broadcasting Rules

Broadcasting works when: (1) dimensions are equal, OR (2) one dimension is 1, OR (3) one array has fewer dimensions. NumPy automatically 'stretches' the smaller array to match. Shape (3,4) can broadcast with (3,1), (1,4), or (4,). This happens automatically - no copying data in memory!

In [ ]:
# Broadcasting examples
arr = np.array([[1, 2, 3],
                [4, 5, 6]])
scalar = 10
row = np.array([10, 20, 30])

print('Array + scalar:', (arr + scalar).tolist())  # Element-wise array operation
print('Array + row:', (arr + row).tolist())  # Element-wise array operation

**Result:** Scalar 10 broadcast to all elements. Row [10,20,30] broadcast to both rows: [1,2,3]+[10,20,30]=[11,22,33], same for row 2. No explicit loops needed!

## 2.2 Data Normalization with Broadcasting

Normalizing data (subtracting mean, dividing by std) is perfect for broadcasting. Calculate mean per column (axis=0), then subtract using broadcasting. This centers data around zero with unit variance - essential for machine learning algorithms. Broadcasting makes this operation clean and efficient.

In [ ]:
# Student test scores
scores = np.array([[85, 92, 78],
                   [72, 68, 75],
                   [95, 98, 92]])
mean = scores.mean(axis=0)
std = scores.std(axis=0)
normalized = (scores - mean) / std  # Element-wise array operation
print('Means:', mean)
print('Normalized:\n', normalized)

**Result:** Each column (test) now has mean≈0 and std≈1. Broadcasting applied mean and std to every row automatically. This standardizes data for fair comparison!

### Exercise: Temperature Normalization

Normalize daily temperatures (subtract mean, divide by std) for each city.

In [ ]:
temps = np.array([[72, 68, 75],
                  [75, 70, 78],
                  [71, 67, 73],
                  [78, 72, 80]])
# Your code here (axis matters!):


In [ ]:
# Solution
mean_per_city = temps.mean(axis=0)
std_per_city = temps.std(axis=0)
normalized_temps = (temps - mean_per_city) / std_per_city  # Element-wise array operation
print('Normalized (mean≈0, std≈1 per city):\n', normalized_temps)

**Solution:** axis=0 gives mean per city (across days). Broadcasting subtracts and divides correctly. Each city now has standardized temperatures!

---
# Part 3: Random Number Generation

Random numbers are essential for simulations, sampling, testing, and machine learning. NumPy's modern API uses np.random.default_rng() to create a generator object that produces high-quality random numbers. This replaces older functions like np.random.rand(). The generator approach allows better control over randomness, reproducibility through seeding, and access to various probability distributions.

## 3.1 Creating a Random Generator

The default_rng() function creates a random number generator. Think of it as a machine that produces unpredictable numbers on demand. Once created, you call methods like .random() for [0,1) floats, .integers() for whole numbers, or .normal() for bell curve distributions. This object-oriented approach is more flexible than old global functions.

In [ ]:
# Create random generator
rng = np.random.default_rng()

# Generate random floats [0, 1)
rand_floats = rng.random(5)
print('Random floats:', rand_floats)

# Random integers
rand_ints = rng.integers(1, 100, size=5)
print('Random integers:', rand_ints)

**Result:** random() gives uniform floats between 0 and 1. integers(low, high, size) gives whole numbers. Each run produces different values!

## 3.2 Seeding for Reproducibility

Seeding makes 'random' numbers repeatable - crucial for debugging, testing, and scientific reproducibility. Pass an integer seed to default_rng(seed). Same seed = same sequence. Think of it like replaying a recording - the randomness is predetermined but appears random. This lets others reproduce your exact results.

In [ ]:
# With seed - reproducible
rng1 = np.random.default_rng(42)
rng2 = np.random.default_rng(42)

print('RNG1:', rng1.random(3))
print('RNG2:', rng2.random(3))  # Same!

# Without seed - different every time
print('No seed:', np.random.default_rng().random(3))  # Create random number generator

**Result:** Both rng1 and rng2 with seed=42 produced identical numbers! Use seeds in scientific work for reproducibility.

### Exercise: Simulate Dice Rolls

Simulate rolling two 6-sided dice 10 times. Calculate how many times the sum is 7.

In [ ]:
rng = np.random.default_rng(42)
# Your code here:


In [ ]:
# Solution
dice1 = rng.integers(1, 7, size=10)
dice2 = rng.integers(1, 7, size=10)
sums = dice1 + dice2
sevens = (sums == 7).sum()  # Create boolean mask for filtering
print(f'Rolled 7: {sevens} times out of 10')

---
# Part 4: Array-Oriented Programming

Array-oriented programming means expressing operations on entire arrays at once instead of writing loops. NumPy provides functions like np.where() for conditional selection and np.meshgrid() for creating coordinate grids. This vectorized approach is faster, clearer, and more Pythonic than explicit loops. Think declaratively: describe what you want, not how to compute it step-by-step.

## 4.1 Vectorized Conditionals with np.where()

np.where(condition, value_if_true, value_if_false) is like Excel's IF function for arrays. It evaluates a condition for every element and picks values accordingly. No loops needed! This replaces pattern: for i in range(n): if condition[i]: result[i]=x else: result[i]=y. Much cleaner and 10-100x faster!

In [ ]:
# Temperature classification
temps = np.array([68, 75, 90, 79, 95, 72])

# Classify as hot (>=80) or comfortable
classify = np.where(temps >= 80, 'hot', 'comfortable')  # Create boolean mask for filtering
print('Temperatures:', temps)
print('Classification:', classify)

**Result:** np.where() checked each temp and assigned labels. Element-wise IF logic without loops! This is the NumPy way.

### Exercise: Grade Assignment

Convert numeric scores to letter grades: >=90='A', >=80='B', >=70='C', else='F'. Use nested np.where().

In [ ]:
scores = np.array([85, 92, 67, 78, 95, 73, 88])
# Your code here (hint: nest where() calls):


In [ ]:
# Solution
grades = np.where(scores >= 90, 'A',  # Create boolean mask for filtering
           np.where(scores >= 80, 'B',  # Create boolean mask for filtering
           np.where(scores >= 70, 'C', 'F')))  # Create boolean mask for filtering
print('Scores:', scores)
print('Grades:', grades)

---
# Part 5: Linear Algebra Operations - CRITICAL FOR ASSIGNMENT 4

Linear algebra operations are fundamental for data science, machine learning, and scientific computing. NumPy provides powerful functions for matrix operations, solving systems of equations, fitting polynomials to data trends, and calculating correlations between variables. Two functions are CRITICAL for Assignment 4 Problem 7: np.polyfit() fits polynomial curves to data, and np.corrcoef() calculates correlation matrices showing relationships between variables.

## 5.1 Polynomial Fitting with np.polyfit() - ASSIGNMENT 4 PROBLEM 7!

np.polyfit(x, y, degree) fits a polynomial of specified degree to your data points. Think of it like drawing the best-fit curve through scattered points - it finds coefficients that minimize error. Degree 1 gives a straight line (slope and intercept), degree 2 gives a parabola, degree 3 a cubic curve, etc. This is essential for trend analysis, forecasting future values, and understanding data relationships. You'll use this in Assignment 4!

In [ ]:
# Linear fit (degree 1): y = mx + b
x = np.array([1, 2, 3, 4, 5])
y = np.array([2.1, 3.9, 6.2, 7.8, 10.1])

# Fit line to data
coeffs = np.polyfit(x, y, 1)
print('Coefficients [m, b]:', coeffs)
m, b = coeffs
print(f'Equation: y = {m:.2f}x + {b:.2f}')  # Element-wise array operation

**Result:** polyfit returned [m, b] where m=2.00 is slope and b=0.08 is intercept. The best-fit line is y = 2.00x + 0.08. This captures the upward trend in the data!

In [ ]:
# Make predictions with fitted model
x_new = np.array([6, 7, 8])
y_pred = m * x_new + b
print(f'Predictions for x={x_new}: y={y_pred}')

**Prediction:** Using our fitted line, we predict future values! For x=6, y≈12.08. This is how forecasting works!

### Exercise: Temperature Trend Analysis

You have daily temperatures over 6 days. Fit a linear trend and predict day 7's temperature.

In [ ]:
days = np.array([1, 2, 3, 4, 5, 6])
temps = np.array([72, 75, 77, 79, 81, 83])
# Your code: fit, extract coefficients, predict day 7


In [ ]:
# Solution
coeffs = np.polyfit(days, temps, 1)
slope, intercept = coeffs
day_7_temp = slope * 7 + intercept
print(f'Trend: {slope:.2f} degrees/day')
print(f'Day 7 prediction: {day_7_temp:.1f} degrees')

**Solution:** Slope 2.2 means temps rising 2.2°/day. Predicting day 7: ~85.4°. This is exactly what Assignment 4 Problem 7 requires!

## 5.2 Quadratic Fitting - More Complex Curves

Degree 2 fits a parabola (y = ax² + bx + c). This captures curved relationships that lines can't. Use when data has curvature - increasing rates of change, peak/valley patterns. polyfit returns [a, b, c] coefficients in descending power order. Higher degrees fit more complex curves but risk overfitting!

In [ ]:
# Quadratic data with curve
x = np.array([0, 1, 2, 3, 4, 5])
y = np.array([1, 2.2, 4.8, 9.1, 15.2, 23])

# Fit parabola
coeffs = np.polyfit(x, y, 2)
a, b, c = coeffs
print(f'Quadratic: y = {a:.2f}x² + {b:.2f}x + {c:.2f}')  # Element-wise array operation

**Result:** Fitted y = 0.99x² + 0.21x + 1.04. The x² term captures the upward curve. Use np.poly1d(coeffs) to evaluate easily!

## 5.3 Correlation Analysis with np.corrcoef() - ASSIGNMENT 4 PROBLEM 7!

np.corrcoef(x, y) calculates Pearson correlation coefficient between variables. Values range -1 to +1: +1 means perfect positive correlation (both increase together), -1 means perfect negative (one increases, other decreases), 0 means no linear relationship. This identifies which variables are related - crucial for feature selection, understanding data structure, and finding redundancies. You'll use this in Assignment 4!

In [ ]:
# Study hours vs test scores
hours = np.array([2, 3, 4, 5, 6, 7, 8])
scores = np.array([65, 70, 75, 80, 85, 88, 92])

# Calculate correlation
corr_matrix = np.corrcoef(hours, scores)
print('Correlation matrix:')
print(corr_matrix)
print(f'\nCorrelation: {corr_matrix[0,1]:.3f}')

**Result:** Correlation 0.996 means very strong positive relationship! More study hours → higher scores. Matrix is symmetric: [0,1] = [1,0]. Diagonal is always 1.0 (variable correlates perfectly with itself).

### Exercise: Temperature vs Ice Cream Sales

Calculate correlation between daily temperature and ice cream sales. Interpret the result.

In [ ]:
temps = np.array([72, 75, 80, 85, 90, 78, 82])
sales = np.array([150, 180, 220, 280, 320, 190, 240])
# Your code: calculate correlation


In [ ]:
# Solution
corr = np.corrcoef(temps, sales)[0, 1]
print(f'Correlation: {corr:.3f}')
if corr > 0.7:
    print('Strong positive: Higher temps → more sales!')
elif corr > 0.3:
    print('Moderate positive correlation')
else:
    print('Weak or no correlation')

**Solution:** Correlation ≈0.99 - extremely strong! Temperature is an excellent predictor of sales. This is what Assignment 4 Problem 7 asks you to analyze!

## 5.4 Multiple Variable Correlation

Pass multiple arrays as rows to get full correlation matrix. This shows pairwise correlations between all variables simultaneously. Perfect for exploratory data analysis - quickly see which features relate to each other and to your target variable. The matrix is always symmetric with 1.0 diagonal.

In [ ]:
# Three variables: temp, ice cream, sunglasses
temps = np.array([72, 80, 85, 90, 78])
ice_cream = np.array([150, 220, 280, 320, 190])
sunglasses = np.array([20, 35, 45, 55, 28])

# Stack as rows for corrcoef
data = np.array([temps, ice_cream, sunglasses])
corr_matrix = np.corrcoef(data)
print('Correlation matrix (3x3):')
print(corr_matrix)

**Result:** All three variables strongly correlated! [0,1]=0.99 (temp vs ice cream), [0,2]=0.99 (temp vs sunglasses), [1,2]=0.99 (ice cream vs sunglasses). All driven by temperature!

---
# Part 6: File I/O for Arrays

Saving and loading arrays lets you persist computational results, share data with colleagues, and resume analysis later. NumPy provides efficient binary format (.npy) that preserves exact values and datatypes. Much faster and more accurate than text files! Use np.save() for single arrays, np.savez() for multiple arrays in one archive.

## 6.1 Saving and Loading Single Arrays

np.save(filename, array) saves to .npy format. np.load(filename) reads it back. Binary format is fast, compact, and preserves precision perfectly. Unlike CSV, no rounding errors or parsing issues! The file automatically gets .npy extension if you don't specify it.

In [ ]:
# Create and save array
data = np.array([[1, 2, 3], [4, 5, 6]])
np.save('my_array.npy', data)  # Save array to binary file
print('Saved array to my_array.npy')

# Load it back
loaded = np.load('my_array.npy')
print('Loaded array:')
print(loaded)
print('Arrays equal:', np.array_equal(data, loaded))

**Result:** Saved and loaded perfectly! No data loss, exact match. This is how you save computation results for later use.

## 6.2 Saving Multiple Arrays

np.savez(filename, arr1=array1, arr2=array2, ...) saves multiple arrays in compressed archive. Access them by name when loading. Perfect for related datasets - features and labels, multiple experiments, time series data. The .npz file is like a ZIP containing multiple .npy files.

In [ ]:
# Save multiple arrays
features = np.array([[1, 2], [3, 4]])
labels = np.array([0, 1])
np.savez('dataset.npz', X=features, y=labels)
print('Saved features and labels')

# Load back
data = np.load('dataset.npz')
print('Features:', data['X'])
print('Labels:', data['y'])

**Result:** Both arrays saved in one file, accessed by names 'X' and 'y'. Organized and efficient!

---
# Part 7: Random Walks - NumPy's Power Demonstrated

Random walks model many real phenomena: stock prices, molecular motion, animal foraging, game outcomes. A random walk takes random steps (up/down, left/right) and we analyze the resulting path. NumPy excels here - simulating thousands of walks simultaneously with incredible speed. This demonstrates everything you learned: random generation, cumsum, boolean operations, and vectorization.

## 7.1 Single Random Walk

A simple random walk: start at 0, take random steps +1 or -1, track position over time. Use random integers for steps, cumsum for position tracking. This models a fair game - neither player has advantage. Will we end up ahead or behind after 1000 steps? NumPy makes this trivial!

In [ ]:
# Single random walk: 1000 steps
rng = np.random.default_rng(42)
steps = rng.choice([-1, 1], size=1000)
walk = np.cumsum(steps)

print(f'Final position: {walk[-1]}')
print(f'Max position: {walk.max()}')  # Find minimum/maximum value
print(f'Min position: {walk.min()}')  # Find minimum/maximum value

**Result:** After 1000 random steps, we ended at position {walk[-1]}. Reached maximum {walk.max()} and minimum {walk.min()}. Pure randomness creates interesting paths!

## 7.2 Simulating 5000 Walks Simultaneously - NumPy's Power!

Now simulate 5000 random walks at once! Each walk is 1000 steps. Use 2D array: rows=walks, columns=steps. NumPy handles all 5000 walks simultaneously with vectorized operations. This would take forever with loops - NumPy does it instantly! This showcases the power of array-oriented programming.

In [ ]:
# 5000 walks, 1000 steps each
rng = np.random.default_rng(42)
steps = rng.choice([-1, 1], size=(5000, 1000))
walks = np.cumsum(steps, axis=1)

print(f'Shape: {walks.shape}')
print(f'Simulated 5 million steps instantly!')

**Result:** Created 5000x1000 array = 5 million random steps, processed in milliseconds! Each row is a complete 1000-step random walk.

## 7.3 Analyzing 5000 Walks

Now analyze all 5000 walks: How many crossed +30 or -30? When did each cross? Use boolean operations and argmax to find first crossing time. This demonstrates boolean indexing, aggregation, and NumPy's analytical power.

In [ ]:
# Find walks that crossed +30 or -30
crossed_30 = (np.abs(walks) >= 30).any(axis=1)  # Create boolean mask for filtering
num_crossed = crossed_30.sum()
print(f'Walks crossing ±30: {num_crossed} / 5000')  # Element-wise array operation

# First crossing time for walks that crossed
first_cross = (np.abs(walks) >= 30).argmax(axis=1)  # Create boolean mask for filtering
avg_cross_time = first_cross[crossed_30].mean()
print(f'Average crossing time: {avg_cross_time:.1f} steps')

**Result:** Out of 5000 walks, {num_crossed} crossed ±30 boundary. Those that crossed did so in average {avg_cross_time:.1f} steps. Analyzing 5000 walks took milliseconds - this is NumPy's power!

**Key Insight:** Random walks demonstrate everything from this lecture: random generation, cumulative operations, boolean logic, statistical analysis, and vectorization. NumPy processes millions of values faster than Python could process thousands. This is why NumPy is essential for data science!

---
# Lecture Summary

## Key Concepts Mastered:

**Matrix Operations:** Transpose (.T), matrix multiplication (@), swapaxes()

**Broadcasting:** Automatic shape matching for elegant operations, data normalization

**Random Numbers:** Modern default_rng() API, seeding for reproducibility, distributions

**Array-Oriented:** Vectorized conditionals (np.where()), coordinate grids (np.meshgrid())

**Linear Algebra - CRITICAL FOR ASSIGNMENT 4:**
- **np.polyfit()**: Fit polynomials to data trends, make predictions
- **np.corrcoef()**: Calculate correlations, identify relationships

**File I/O:** Save/load arrays efficiently with .npy and .npz formats

**Random Walks:** Comprehensive demonstration of NumPy's power - 5000 simultaneous simulations

## Assignment 4 Connection:

**Problem 7 DIRECTLY USES:**
- np.polyfit() for fitting trend lines to data
- np.corrcoef() for calculating variable correlations
- Both covered extensively in this lecture!

**Other Problems:**
- Problem 6: Broadcasting for normalization
- Problem 5: np.where() for conditional logic


**Excellent work - you're now prepared for Assignment 4 and ready for pandas!**